In [1]:
import requests
import pandas as pd
import numpy as np
import tensorflow as tf

In [253]:
tf.__version__

'1.3.0'

In [3]:
from bokeh.plotting import figure, show
from bokeh.io import output_notebook
from bokeh.embed import components 

In [ ]:
from ediblepickle import checkpoint
import os
import urllib

In [4]:
url = 'https://data.cityofnewyork.us/resource/fhrw-4uyv.json'
url3 = 'https://data.cityofnewyork.us/resource/fhrw-4uyv.json?city=NEW YORK&$limit=3000&$where=agency in("DEP","DOB","DOT","HPD","NYPD","DSNY","FDNY","DPR")'
url_2010 = 'https://data.cityofnewyork.us/resource/mwbr-9zz9.json'
url_2011 = 'https://data.cityofnewyork.us/resource/knik-dax9.json'
url_2012 = 'https://data.cityofnewyork.us/resource/6nxj-n6t5.json'
url_2013 = 'https://data.cityofnewyork.us/resource/e8jc-rs3b.json'
url_2014 = 'https://data.cityofnewyork.us/resource/f364-y3pv.json'
url_2015 = 'https://data.cityofnewyork.us/resource/hemm-82xw.json'
url_2009 = 'https://data.cityofnewyork.us/resource/76rq-desm.json'
url_2008 = 'https://data.cityofnewyork.us/resource/ttef-akmb.json'
url_2007 = 'https://data.cityofnewyork.us/resource/bjsb-smxa.json'
url_2006 = 'https://data.cityofnewyork.us/resource/txvy-sgqz.json'
url_2005 = 'https://data.cityofnewyork.us/resource/xk2u-49gx.json'
url_2004 = 'https://data.cityofnewyork.us/resource/fred-eu2a.json'

### Retrieve 311 data in real-time

In [5]:
afterdate = r"'2017-01-01'"

In [6]:

cache_dir = 'cache'
if not os.path.exists(cache_dir):
    os.mkdir(cache_dir)

@checkpoint(key=lambda args, kwargs: urllib.parse.quote(args[0]) + '_' + str(args[1]) + '.p', work_dir=cache_dir)#, refresh=True)
def get_data(city, rows, where, date):
    params = { #'format'        :'json', 
                '$order':        'created_date',
               '$limit':         rows, 
               'city' :          city,
                '$select':		'created_date,closed_date,agency,incident_zip,complaint_type,descriptor,latitude,longitude',
                '$where':        'created_date>='+date}
                #'$where' :         where}
    print ('making API request...')
    result = requests.get(url, params=params)#.encode('utf-8')
    print ('API request complete.')
    return result


In [7]:
city = 'NEW YORK'
calls =300000
agencies = ("DEP","DOB","DOT","HPD","NYPD","DSNY","FDNY","DPR")

In [8]:
#str([str(x) for x in agencies])
agencyList = ','.join('"%s"' % x for x in agencies)

In [9]:
agencyList

'"DEP","DOB","DOT","HPD","NYPD","DSNY","FDNY","DPR"'

In [10]:
r = get_data(city,calls,'agency in('+agencyList+')', afterdate)
#r = requests.get(url3)

In [11]:
#r.json()

### convert to pandas database
fix columns, lat/longs, times, etc

In [332]:
df = pd.read_json(r.text, convert_dates=True)

In [333]:
print(df.head())

  agency              closed_date complaint_type             created_date  \
0  DOHMH  2016-12-05T00:00:00.000         Rodent  2017-01-01T00:00:00.000   
1  DOHMH  2017-01-03T00:00:00.000         Rodent  2017-01-01T00:00:00.000   
2  DOHMH  2016-12-28T00:00:00.000         Rodent  2017-01-01T00:00:00.000   
3  DOHMH  2017-01-05T00:00:00.000         Rodent  2017-01-01T00:00:00.000   
4  DOHMH  2016-11-23T00:00:00.000         Rodent  2017-01-01T00:00:00.000   

       descriptor incident_zip   latitude  longitude  
0    Rat Sighting        10010  40.737384 -73.983719  
1  Mouse Sighting        10010  40.743031 -73.989156  
2    Rat Sighting        10009  40.721102 -73.981699  
3    Rat Sighting        10028  40.777632 -73.951144  
4  Mouse Sighting        10012  40.728067 -73.999322  


In [14]:
print(len(df))

300000


In [15]:
df.columns.tolist()

['agency',
 'closed_date',
 'complaint_type',
 'created_date',
 'descriptor',
 'incident_zip',
 'latitude',
 'longitude']

In [16]:
for col in df.columns.tolist():
    print(col),

agency
closed_date
complaint_type
created_date
descriptor
incident_zip
latitude
longitude


In [17]:
'index' in df

False

In [334]:
#clean up database
collist = ['created_date', 'closed_date', 'agency', 'incident_zip', 'complaint_type', 'latitude', 'longitude']
newcols = ['created', 'closed', 'agency','zip', 'complaint', 'lat', 'long']
df = df[collist]
#print(df.columns.values())
#rename cols
df.rename(columns=dict(zip(collist, newcols)), inplace=True)
#df.rename(columns={newcols[i] for i,x in enumerate(df.columns)})
#df.rename(columns={lambda i,x: x: newcols[i]}, inplace=True)
#df.columns = map(str.lower, df.columns)
print(df.columns[0])

created


In [13]:
df.columns.tolist()

['created', 'closed', 'agency', 'zip', 'complaint', 'lat', 'long']

In [335]:
del df['closed']

In [336]:
import datetime
startdate = min(df.created)#.iloc[0]
#print(min(df.created))
#print(startdate.year, startdate.month, startdate.day)
startdate = datetime.datetime.strptime(startdate, '%Y-%m-%dT%H:%M:%S.%f')
#if verbose>0: print('%d-%d-%d' % (startdate.month, startdate.day, startdate.year))
startdate = str(startdate.month)+'/'+str(startdate.day)+'/'+str(startdate.year)
enddate = max(df['created'])#.iloc[-1]
enddate = datetime.datetime.strptime(enddate, '%Y-%m-%dT%H:%M:%S.%f')
enddate = str(enddate.month)+'/'+str(enddate.day)+'/'+str(enddate.year)
#if verbose>0: print(enddate); print(max(df.created)); print(min(df.created))
print(startdate, enddate)

1/1/2017 8/29/2017


In [337]:
df.head()

created agency    zip complaint        lat       long
0  2017-01-01T00:00:00.000  DOHMH  10010    Rodent  40.737384 -73.983719
1  2017-01-01T00:00:00.000  DOHMH  10010    Rodent  40.743031 -73.989156
2  2017-01-01T00:00:00.000  DOHMH  10009    Rodent  40.721102 -73.981699
3  2017-01-01T00:00:00.000  DOHMH  10028    Rodent  40.777632 -73.951144
4  2017-01-01T00:00:00.000  DOHMH  10012    Rodent  40.728067 -73.999322

In [338]:
df.tail()

created agency    zip             complaint  \
299995  2017-08-29T19:09:38.000   NYPD  10033   Noise - Residential   
299996  2017-08-29T19:10:00.000   DSNY  10025  Sanitation Condition   
299997  2017-08-29T19:12:22.000    DCA  10019    Consumer Complaint   
299998  2017-08-29T19:13:48.000   NYPD  10032   Noise - Residential   
299999  2017-08-29T19:16:47.000   NYPD  10034    Noise - Commercial   

              lat       long  
299995  40.846963 -73.938461  
299996  40.807154 -73.965944  
299997  40.768604 -73.987364  
299998  40.844179 -73.941427  
299999  40.867404 -73.921015

In [339]:
#find small pockets of high incidence of 311 calls
#from decimal import *
#getcontext().prec = 2
df['lat']=df['lat'].apply(lambda x:round(x, 3))#, axis=1)
df['long']=df['long'].apply(lambda x:round(x, 3))

In [27]:
df.created[0]

Timestamp('2017-01-01 00:00:00')

In [340]:
df['created'] = pd.to_datetime(df.created, infer_datetime_format=True, errors='coerce')

In [341]:
#df.created.dt.date
df.created[0]

Timestamp('2017-01-01 00:00:00')

In [342]:
df.head()

created agency    zip complaint     lat    long
0 2017-01-01  DOHMH  10010    Rodent  40.737 -73.984
1 2017-01-01  DOHMH  10010    Rodent  40.743 -73.989
2 2017-01-01  DOHMH  10009    Rodent  40.721 -73.982
3 2017-01-01  DOHMH  10028    Rodent  40.778 -73.951
4 2017-01-01  DOHMH  10012    Rodent  40.728 -73.999

In [343]:
#stats on lat/long
df.describe()

lat           long
count  289819.000000  289819.000000
mean       40.781931     -73.965820
std         0.046149       0.025521
min        40.678000     -74.045000
25%        40.742000     -73.987000
50%        40.779000     -73.966000
75%        40.819000     -73.943000
max        40.881000     -73.726000

In [344]:
round(min(df.lat), 3), max(df.lat)

(40.677999999999997, 40.881)

In [345]:
minlat, maxlat, minlong, maxlong = min(df.lat), max(df.lat), min(df.long), max(df.long)

In [346]:
df['latlong'] = list(zip(df.lat, df.long))

In [347]:
df = df.dropna()

In [348]:
latlongs = set(df.latlong.values)

In [349]:
len(latlongs)

4966

In [5]:
#if this is oldcode
oldcode = 1
if oldcode==0:
    print("not executing this cell")

In [ ]:
#this cell not used
if oldcode==0:
    #df.drop('EDC', axis=0, inplace=True)
    df = df[df.agency != "EDC"]
    df = df[df.agency != "DCA"]
    df = df[df.agency != "DOF"]
    df = df[df.agency != "DFTA"]
    df = df[df.agency != "3-1-1"]
    df = df[df.agency != "DOE"]
    df = df[df.agency != "NYCEM"]
    df = df[df.agency != "DOITT"]

In [350]:
df = df.dropna()

In [33]:
df.created[2500].hour

17

### fix times
old idea was to convert times to cyclical, to make sure times that were close to each other (11:59pm and midnight) would be recognized as such and not split off from one another in the algorithm, same with the end of one month and beginning of next, as well as start/end of weekday.

-realized this still wouldn't work well, and tensorflow is deep enough to see patterns anyway

-ended up splitting time into hour, day, date, month, and year, each with own columns

In [351]:
df['year'] = df.created.apply(lambda x: x.year)

In [357]:
list((1,3,5,7,8,10,12))

[1, 3, 5, 7, 8, 10, 12]

In [358]:
#df['hourofday'] = df.created.apply(lambda x: x.hour + x.minute/60.0)
df['hour'] = df.created.apply(lambda x: x.hour + x.minute/60.0)
df['day'] = df.created.apply(lambda x: x.weekday())
df['date'] = df.created.apply(lambda x: x.day) 

In [364]:
df.created[0].month#.dtype

1

In [369]:
df['month'] = df.created.apply(lambda x: (x.month + x.day/31.0) if x.month in [1,3,5,7,8,10,12] else (x.month + x.day/30.0)) #really should -1 from month and day to start from 0

In [370]:
df.head(10)

created agency    zip                       complaint     lat  \
0 2017-01-01 00:00:00  DOHMH  10010                          Rodent  40.737   
1 2017-01-01 00:00:00  DOHMH  10010                          Rodent  40.743   
2 2017-01-01 00:00:00  DOHMH  10009                          Rodent  40.721   
3 2017-01-01 00:00:00  DOHMH  10028                          Rodent  40.778   
4 2017-01-01 00:00:00  DOHMH  10012                          Rodent  40.728   
5 2017-01-01 00:00:00  DOHMH  10003                          Rodent  40.727   
6 2017-01-01 00:00:00  DOHMH  10010                          Rodent  40.737   
7 2017-01-01 00:00:00  DOHMH  10009  Unsanitary Animal Pvt Property  40.730   
8 2017-01-01 00:00:00  DOHMH  10030  Unsanitary Animal Pvt Property  40.818   
9 2017-01-01 00:03:41   NYPD  10040             Noise - Residential  40.864   

     long            latlong  year  hour  day  date     month  
0 -73.984  (40.737, -73.984)  2017  0.00    6     1  1.032258  
1 -73.989  (40.743, -73.989)  2017  0.00    6     1  1.032258  
2 -73.982  (40.721, -73.982)  2017  0.00    6     1  1.032258  
3 -73.951  (40.778, -73.951)  2017  0.00    6     1  1.032258  
4 -73.999  (40.728, -73.999)  2017  0.00    6     1  1.032258  
5 -73.990   (40.727, -73.99)  2017  0.00    6     1  1.032258  
6 -73.984  (40.737, -73.984)  2017  0.00    6     1  1.032258  
7 -73.975   (40.73, -73.975)  2017  0.00    6     1  1.032258  
8 -73.939  (40.818, -73.939)  2017  0.00    6     1  1.032258  
9 -73.927  (40.864, -73.927)  2017  0.05    6     1  1.032258

In [371]:
#rodent, food poisoning, animal all lumped under hour/minute = 0....skewing data.
df[df.month == 2][df.day==2][df.hour==0]

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:2: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  


Empty DataFrame
Columns: [created, agency, zip, complaint, lat, long, latlong, year, hour, day, date, month]
Index: []

In [298]:
df.groupby(['month','day','hour','latlong']).count()

created  agency  zip  complaint  lat  long  \
month day hour latlong                                                         
1     0   0    (40.704, -74.009)        1       1    1          1    1     1   
               (40.705, -74.01)         1       1    1          1    1     1   
               (40.706, -74.009)        1       1    1          1    1     1   
               (40.707, -74.002)        1       1    1          1    1     1   
               (40.708, -74.011)        1       1    1          1    1     1   
               (40.708, -74.005)        1       1    1          1    1     1   
               (40.708, -74.002)        1       1    1          1    1     1   
               (40.709, -74.006)        1       1    1          1    1     1   
               (40.71, -74.007)         1       1    1          1    1     1   
               (40.711, -74.009)        1       1    1          1    1     1   
               (40.712, -74.008)        1       1    1          1    1     1   
               (40.712, -73.987)        1       1    1          1    1     1   
               (40.713, -74.007)        2       2    2          2    2     2   
               (40.713, -73.995)        1       1    1          1    1     1   
               (40.713, -73.984)        1       1    1          1    1     1   
               (40.714, -73.998)        1       1    1          1    1     1   
               (40.715, -74.005)        1       1    1          1    1     1   
               (40.715, -74.002)        1       1    1          1    1     1   
               (40.715, -73.992)        1       1    1          1    1     1   
               (40.716, -74.005)        1       1    1          1    1     1   
               (40.717, -73.995)        1       1    1          1    1     1   
               (40.717, -73.993)        1       1    1          1    1     1   
               (40.717, -73.99)         1       1    1          1    1     1   
               (40.717, -73.987)        1       1    1          1    1     1   
               (40.718, -73.992)        1       1    1          1    1     1   
               (40.718, -73.989)        1       1    1          1    1     1   
               (40.718, -73.988)        1       1    1          1    1     1   
               (40.718, -73.987)        1       1    1          1    1     1   
               (40.719, -74.002)        1       1    1          1    1     1   
               (40.719, -73.997)        1       1    1          1    1     1   
...                                   ...     ...  ...        ...  ...   ...   
8     6   23   (40.859, -73.93)         2       2    2          2    2     2   
               (40.861, -73.929)        1       1    1          1    1     1   
               (40.861, -73.928)        1       1    1          1    1     1   
               (40.862, -73.929)        3       3    3          3    3     3   
               (40.862, -73.928)        2       2    2          2    2     2   
               (40.862, -73.926)        2       2    2          2    2     2   
               (40.862, -73.924)        1       1    1          1    1     1   
               (40.863, -73.93)         1       1    1          1    1     1   
               (40.863, -73.928)        2       2    2          2    2     2   
               (40.863, -73.92)         1       1    1          1    1     1   
               (40.864, -73.928)        2       2    2          2    2     2   
               (40.864, -73.926)        5       5    5          5    5     5   
               (40.864, -73.924)       12      12   12         12   12    12   
               (40.864, -73.923)        1       1    1          1    1     1   
               (40.864, -73.917)        1       1    1          1    1     1   
               (40.865, -73.922)        3       3    3          3    3     3   
               (40.865, -73.92)         1       1    1          1    1     1   
               (40.866, -73.93)   

In [372]:
df.groupby(['complaint']).count().nlargest(25,columns='created')

created  agency    zip    lat   long  latlong  \
complaint                                                                      
Noise - Residential              33105   33105  33105  33105  33105    33105   
HEAT/HOT WATER                   25086   25086  25086  25086  25086    25086   
Noise - Street/Sidewalk          19802   19802  19802  19802  19802    19802   
Noise                            18587   18587  18587  18587  18587    18587   
Illegal Parking                  12900   12900  12900  12900  12900    12900   
Noise - Commercial               12043   12043  12043  12043  12043    12043   
Homeless Person Assistance       12013   12013  12013  12013  12013    12013   
Street Condition                 10775   10775  10775  10775  10775    10775   
UNSANITARY CONDITION              9593    9593   9593   9593   9593     9593   
PAINT/PLASTER                     7898    7898   7898   7898   7898     7898   
Water System                      7653    7653   7653   7653   7653     7653   
Noise - Vehicle                   7002    7002   7002   7002   7002     7002   
PLUMBING                          6988    6988   6988   6988   6988     6988   
Taxi Complaint                    5563    5563   5563   5563   5563     5563   
Rodent                            5225    5225   5225   5225   5225     5225   
DOOR/WINDOW                       4531    4531   4531   4531   4531     4531   
General Construction/Plumbing     4407    4407   4407   4407   4407     4407   
GENERAL                           4299    4299   4299   4299   4299     4299   
WATER LEAK                        3909    3909   3909   3909   3909     3909   
Dirty Conditions                  3738    3738   3738   3738   3738     3738   
FLOORING/STAIRS                   3394    3394   3394   3394   3394     3394   
Consumer Complaint                3138    3138   3138   3138   3138     3138   
ELECTRIC                          3048    3048   3048   3048   3048     3048   
Broken Muni Meter                 2966    2966   2966   2966   2966     2966   
Food Establishment                2619    2619   2619   2619   2619     2619   

                                year   hour    day   date  month  
complaint                                                         
Noise - Residential            33105  33105  33105  33105  33105  
HEAT/HOT WATER                 25086  25086  25086  25086  25086  
Noise - Street/Sidewalk        19802  19802  19802  19802  19802  
Noise                          18587  18587  18587  18587  18587  
Illegal Parking                12900  12900  12900  12900  12900  
Noise - Commercial             12043  12043  12043  12043  12043  
Homeless Person Assistance     12013  12013  12013  12013  12013  
Street Condition               10775  10775  10775  10775  10775  
UNSANITARY CONDITION            9593   9593   9593   9593   9593  
PAINT/PLASTER                   7898   7898   7898   7898   7898  
Water System                    7653   7653   7653   7653   7653  
Noise - Vehicle                 7002   7002   7002   7002   7002  
PLUMBING                        6988   6988   6988   6988   6988  
Taxi Complaint                  5563   5563   5563   5563   5563  
Rodent                          5225   5225   5225   5225   5225  
DOOR/WINDOW                     4531   4531   4531   4531   4531  
General Construction/Plumbing   4407   4407   4407   4407   4407  
GENERAL                         4299   4299   4299   4299   4299  
WATER LEAK                      3909   3909   3909   3909   3909  
Dirty Conditions                3738   3738   3738   3738   3738  
FLOORING/STAIRS                 3394   3394   3394   3394   3394  
Consumer Complaint              3138   3138   3138   3138   3138  
ELECTRIC                        3048   3048   3048   3048   3048  
Broken Muni Meter               2966   2966   2966   2966   2966  
Food Establishment              2619   2619   2619   2619   2619

### clarify x (input, features) and y (result) to develop model

### inputs x should be time and location

In [373]:
df.shape

(289759, 12)

In [374]:
# add 'date' when doing predictions over months+ and change month back to without day...
x = df[['lat', 'long','day','hour','month']]#changed dayofweek and hourofday and added date,'year']]#'zip', 

In [375]:
x.head()

lat    long  day  hour     month
0  40.737 -73.984    6   0.0  1.032258
1  40.743 -73.989    6   0.0  1.032258
2  40.721 -73.982    6   0.0  1.032258
3  40.778 -73.951    6   0.0  1.032258
4  40.728 -73.999    6   0.0  1.032258

In [435]:
x.columns

Index(['lat', 'long', 'day', 'hour', 'month'], dtype='object')

In [376]:
#scale inputs
#from sklearn.preprocessing import scale
#x['month'] = x.month.apply(lambda x: scale(x))
from sklearn.preprocessing import MinMaxScaler

scaler = MinMaxScaler(feature_range=(-1,1))

x_scaled = pd.DataFrame(scaler.fit_transform(x), columns=x.columns)


In [377]:
x_scaled.head()

lat      long  day  hour  month
0 -0.418719 -0.617555  1.0  -1.0   -1.0
1 -0.359606 -0.648903  1.0  -1.0   -1.0
2 -0.576355 -0.605016  1.0  -1.0   -1.0
3 -0.014778 -0.410658  1.0  -1.0   -1.0
4 -0.507389 -0.711599  1.0  -1.0   -1.0

In [378]:
x = x_scaled

In [417]:
from sklearn.externals import joblib
scaler_filename = "scaler.save"
joblib.dump(scaler, scaler_filename) 

['scaler.save']

### target y should be agency/complaint

In [379]:
# create one target y class for each sample 
ydf = df.agency + ": " + df.complaint

In [380]:
ydf.head()

0    DOHMH: Rodent
1    DOHMH: Rodent
2    DOHMH: Rodent
3    DOHMH: Rodent
4    DOHMH: Rodent
dtype: object

In [381]:
ydf.values

array(['DOHMH: Rodent', 'DOHMH: Rodent', 'DOHMH: Rodent', ...,
       'DCA: Consumer Complaint', 'NYPD: Noise - Residential',
       'NYPD: Noise - Commercial'], dtype=object)

In [57]:
ydf.tail()

299995     NYPD: Noise - Residential
299996    DSNY: Sanitation Condition
299997       DCA: Consumer Complaint
299998     NYPD: Noise - Residential
299999      NYPD: Noise - Commercial
dtype: object

In [382]:
# one_hot encode target y

#numpy.eye(num_classes)[labels_dense]
y_1h = pd.get_dummies(ydf)#df[['agency', 'complaint']])

In [383]:
# remember feature (class complaints) of each column
features = list(y_1h.columns)

In [384]:
features[0]

'3-1-1: City Vehicle Placard Complaint'

In [385]:
#convert df to np array
y_1h.values

array([[0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       ..., 
       [0, 1, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0],
       [0, 0, 0, ..., 0, 0, 0]], dtype=uint8)

In [386]:
y_1h.values[0].dtype

dtype('uint8')

In [387]:
y_1h = y_1h.astype('int32')

In [388]:
y_1h.values.shape[1]

172

In [436]:
x.values

array([[-0.4187192 , -0.61755484,  1.        , -1.        , -1.        ],
       [-0.35960591, -0.64890283,  1.        , -1.        , -1.        ],
       [-0.57635468, -0.6050157 ,  1.        , -1.        , -1.        ],
       ..., 
       [-0.10344828, -0.63636363, -0.66666669,  0.60111189,  1.        ],
       [ 0.63546801, -0.34796238, -0.66666669,  0.60250175,  1.        ],
       [ 0.86206895, -0.22257054, -0.66666669,  0.60667127,  1.        ]], dtype=float32)

In [389]:
x.values.shape

(289759, 5)

In [390]:
x=x.astype('float32')

In [391]:
x.values[0][3].dtype

dtype('float32')

In [180]:
x.isnull().values.any()

False

In [181]:
x.shape#[1]

(289759, 5)

## tensorflow
### set up model

In [392]:
n_inputs = x.shape[1] #num features
n_hidden1 = n_inputs*100
n_hidden2 = n_inputs*25
n_hidden3 = n_inputs*10
n_hidden4 = n_inputs*5
n_outputs = y_1h.values.shape[1] #num classes

In [393]:
#holds variable for following nn setup code...

X = tf.placeholder(tf.float32, shape=(None, n_inputs), name='X')
y = tf.placeholder(tf.int32, shape=(None), name='y')#tf.one_hot())

In [71]:
y.shape

TensorShape(None)

In [394]:
from tensorflow.contrib.layers import fully_connected
with tf.name_scope("dnn"):
    hidden1 = fully_connected(X, n_hidden1, scope="hidden1", reuse=True)
    hidden2 = fully_connected(hidden1, n_hidden2, scope="hidden2", reuse=True)
    hidden3 = fully_connected(hidden2, n_hidden3, scope="hidden3", reuse=True)
    hidden4 = fully_connected(hidden3, n_hidden4, scope="hidden4", reuse=True)
    logits = fully_connected(inputs=hidden4, num_outputs=n_outputs, scope="outputs", activation_fn=None, reuse=True)

In [395]:
# sparse_softmax_ when not one_hot encoded
with tf.name_scope("loss"):
    xentropy = tf.nn.softmax_cross_entropy_with_logits( logits=logits, labels=y)
    loss = tf.reduce_mean(xentropy, name="loss")

In [396]:
learning_rate = 0.01
with tf.name_scope("train"):
    optimizer = tf.train.GradientDescentOptimizer(learning_rate)
    training_op = optimizer.minimize(loss)

In [397]:
labels = tf.argmax(y, 1)
with tf.name_scope("eval"):
    correct = tf.nn.in_top_k(predictions=logits, targets=labels, k=1) # k:num of top targets
    accuracy = tf.reduce_mean(tf.cast(correct, tf.float32))#tf.float32

In [398]:
# create a node to initialize all variables, and we will also create a Saver to save our trained model parameters to disk:
init = tf.global_variables_initializer()
saver = tf.train.Saver()

### train model

In [399]:
from sklearn.model_selection import train_test_split

X_train, X_test, y_train,  y_test = train_test_split(x.values, y_1h.values, test_size=0.2)

In [400]:
X_train.shape, X_test.shape, y_train.shape, y_test.shape

((231807, 5), (57952, 5), (231807, 172), (57952, 172))

In [401]:
X_train.dtype

dtype('float32')

In [79]:
len(X_train)

231807

In [402]:
num_samples = len(X_train)

In [403]:
n_epochs = 400
batch_size = 64

In [81]:
len(np.zeros((3,6)))

3

In [228]:
def batchiter(iterable, batch_size):
    """
    >>> list(batchiter('ABCDEFG', 3))
    [['A', 'B', 'C'], ['D', 'E', 'F'], ['G']]
    """
    next_batch = np.empty((1, iterable.shape[1]))#[]
    for element in iterable:
        np.vstack((next_batch, element))#next_batch.append(element)
        if len(next_batch) == batch_size:
            batch, next_batch = next_batch, np.empty((1, iterable.shape[1]))#[]
            yield batch
    #if next_batch:
        #yield next_batch

In [404]:
def fetch_batch(batch_index, batch_size):
    X_batch = X_train[batch_index*batch_size : (batch_index+1)*batch_size]
    y_batch = y_train[batch_index*batch_size : (batch_index+1)*batch_size]
    return X_batch, y_batch

In [405]:
import time
now = time.asctime( time.localtime(time.time()) )
print("Local current time :", now)
start = time.time()

# train the model:
with tf.Session() as sess:
    init.run()
    for epoch in range(n_epochs):
        for iteration in range(num_samples // batch_size):
            #X_batch, y_batch = batchiter(X_train, batch_size), batchiter(y_train, batch_size)#X_train.next_batch(batch_size)
            #X_batch = tf.train.batch(tensors=[X_train], batch_size=batch_size, dynamic_pad=False)
            #X_batch = X_train[iteration*batch_size:(iteration+1)*batch_size]
            X_batch, y_batch = fetch_batch(iteration, batch_size)
            #print(X_batch.dtype, X_batch.shape)
            #y_batch = y_train[iteration*batch_size:(iteration+1)*batch_size]
            #print(y_batch.dtype, y_batch.shape)
            sess.run(training_op, feed_dict={X: X_batch, y: y_batch})
        #print('finished first run of batches')
        #sess.run(training_op, feed_dict={X: X_train, y: y_train})
        acc_train = accuracy.eval(feed_dict={X: X_batch, y: y_batch})
        acc_test = accuracy.eval(feed_dict={X: X_test, y: y_test})
        print(epoch, "Train accuracy:", acc_train, "Test accuracy:", acc_test)
        #if epoch%(n_epochs/10) == 0: print(epoch,) 
    save_path = saver.save(sess, "./my_model_final4.ckpt")
    
print("took %d minutes and %d seconds to model." % ((time.time() - start)/60, ((time.time()-start)%60)))
os.system('espeak "model done"')

0 Train accuracy: 0.140625 Test accuracy: 0.135077
1 Train accuracy: 0.21875 Test accuracy: 0.169727
2 Train accuracy: 0.28125 Test accuracy: 0.184239
3 Train accuracy: 0.28125 Test accuracy: 0.189036
4 Train accuracy: 0.28125 Test accuracy: 0.193833
5 Train accuracy: 0.265625 Test accuracy: 0.197249
6 Train accuracy: 0.265625 Test accuracy: 0.198078
7 Train accuracy: 0.265625 Test accuracy: 0.199596
8 Train accuracy: 0.28125 Test accuracy: 0.200304
9 Train accuracy: 0.28125 Test accuracy: 0.201391
10 Train accuracy: 0.28125 Test accuracy: 0.20253
11 Train accuracy: 0.28125 Test accuracy: 0.203099
12 Train accuracy: 0.28125 Test accuracy: 0.204255
13 Train accuracy: 0.296875 Test accuracy: 0.204687
14 Train accuracy: 0.28125 Test accuracy: 0.20498
15 Train accuracy: 0.28125 Test accuracy: 0.205705
16 Train accuracy: 0.28125 Test accuracy: 0.206188
17 Train accuracy: 0.265625 Test accuracy: 0.206844
18 Train accuracy: 0.265625 Test accuracy: 0.207396
19 Train accuracy: 0.265625 Test acc

160 Train accuracy: 0.296875 Test accuracy: 0.237541
161 Train accuracy: 0.296875 Test accuracy: 0.237145
162 Train accuracy: 0.296875 Test accuracy: 0.237421
163 Train accuracy: 0.296875 Test accuracy: 0.237179
164 Train accuracy: 0.296875 Test accuracy: 0.237421
165 Train accuracy: 0.296875 Test accuracy: 0.237455
166 Train accuracy: 0.296875 Test accuracy: 0.237956
167 Train accuracy: 0.296875 Test accuracy: 0.237904
168 Train accuracy: 0.296875 Test accuracy: 0.238076
169 Train accuracy: 0.296875 Test accuracy: 0.238214
170 Train accuracy: 0.296875 Test accuracy: 0.23868
171 Train accuracy: 0.296875 Test accuracy: 0.238939
172 Train accuracy: 0.296875 Test accuracy: 0.238905
173 Train accuracy: 0.296875 Test accuracy: 0.239301
174 Train accuracy: 0.296875 Test accuracy: 0.239733
175 Train accuracy: 0.296875 Test accuracy: 0.239163
176 Train accuracy: 0.296875 Test accuracy: 0.239681
177 Train accuracy: 0.296875 Test accuracy: 0.239664
178 Train accuracy: 0.3125 Test accuracy: 0.239

318 Train accuracy: 0.265625 Test accuracy: 0.250414
319 Train accuracy: 0.265625 Test accuracy: 0.250828
320 Train accuracy: 0.265625 Test accuracy: 0.251122
321 Train accuracy: 0.265625 Test accuracy: 0.251191
322 Train accuracy: 0.265625 Test accuracy: 0.250656
323 Train accuracy: 0.265625 Test accuracy: 0.250552
324 Train accuracy: 0.265625 Test accuracy: 0.250569
325 Train accuracy: 0.265625 Test accuracy: 0.251173
326 Train accuracy: 0.265625 Test accuracy: 0.25088
327 Train accuracy: 0.265625 Test accuracy: 0.251242
328 Train accuracy: 0.265625 Test accuracy: 0.251173
329 Train accuracy: 0.265625 Test accuracy: 0.251346
330 Train accuracy: 0.265625 Test accuracy: 0.251018
331 Train accuracy: 0.265625 Test accuracy: 0.251518
332 Train accuracy: 0.265625 Test accuracy: 0.250897
333 Train accuracy: 0.265625 Test accuracy: 0.251053
334 Train accuracy: 0.265625 Test accuracy: 0.251018
335 Train accuracy: 0.265625 Test accuracy: 0.251553
336 Train accuracy: 0.265625 Test accuracy: 0.2

In [135]:
x.values[600] - x.values[500]

array([-0.11899948, -0.0719986 ,  0.        , -0.52817225,  0.        ,  0.        ], dtype=float32)

In [220]:
x.values[250000]

array([ 0.4187192 , -0.42319748, -0.66666669,  0.39130434,  0.71428573], dtype=float32)

In [255]:
sample = scaler.transform([40.68,-73.961,0,2,2])

/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)


In [221]:
features[np.where(y_1h.values[250000] == 1)[0][0]]

'DSNY: Sanitation Condition'

In [89]:
features[np.where(y_1h.values[1000] == 1)[0][0]]

'HPD: HEAT/HOT WATER'

In [90]:
features[np.where(y_1h.values[50000] == 1)[0][0]]

'NYPD: Noise - Vehicle'

In [222]:
X_new_scaled = x.values[250000].reshape(1, n_inputs)

### predict

In [257]:
# predict
with tf.Session() as sess:
    saver.restore(sess, "./my_model_final3.ckpt")
    #X_new_scaled = [...] # some input scaled in same way
    Z = logits.eval(feed_dict={X: sample.reshape(1,n_inputs)})#X_new_scaled})
    y_pred = np.argmax(Z, axis=1)

INFO:tensorflow:Restoring parameters from ./my_model_final3.ckpt


INFO:tensorflow:Restoring parameters from ./my_model_final3.ckpt


In [258]:
y_pred[0]

156

In [259]:
features[y_pred[0]]

'NYPD: Noise - Residential'

### probability of location having a call at that time:


In [406]:
countlocs = df[['latlong','created']].groupby(['latlong'], as_index=False).count()

In [407]:
countlocs.columns

Index(['latlong', 'created'], dtype='object')

In [113]:
countlocs[countlocs.created > 2]

latlong  created
1      (40.68, -73.897)        6
2     (40.687, -73.726)        3
11    (40.701, -74.013)        5
13    (40.702, -74.016)        7
15    (40.702, -74.013)       44
16    (40.702, -74.012)       18
17    (40.702, -74.011)       26
19    (40.703, -74.016)        6
20    (40.703, -74.014)       17
21    (40.703, -74.013)       62
22    (40.703, -74.012)       51
23    (40.703, -74.011)       17
24     (40.703, -74.01)       26
26    (40.703, -74.008)        3
29    (40.704, -74.014)       31
30    (40.704, -74.013)      105
31    (40.704, -74.012)       74
32    (40.704, -74.011)       24
33     (40.704, -74.01)       52
34    (40.704, -74.009)       44
35    (40.704, -74.008)       24
36    (40.704, -74.007)        7
37    (40.704, -74.006)       15
38    (40.705, -74.018)        8
39    (40.705, -74.017)       37
40    (40.705, -74.016)       37
41    (40.705, -74.015)       38
42    (40.705, -74.014)       69
43    (40.705, -74.013)       51
44    (40.705, -74.012)       53
...                 ...      ...
4926  (40.872, -73.918)      113
4927  (40.872, -73.917)       52
4928  (40.872, -73.916)       18
4929  (40.872, -73.915)       15
4931  (40.872, -73.913)       34
4933  (40.872, -73.911)        3
4935  (40.873, -73.919)       53
4936  (40.873, -73.918)      243
4938  (40.874, -73.928)        4
4940  (40.874, -73.911)        6
4941   (40.874, -73.91)        8
4942  (40.874, -73.909)       11
4943  (40.874, -73.908)       10
4944  (40.875, -73.913)        3
4945  (40.875, -73.912)      186
4946  (40.875, -73.911)      251
4947   (40.875, -73.91)       12
4948  (40.875, -73.909)       44
4949  (40.876, -73.913)       13
4950  (40.876, -73.912)      159
4951  (40.876, -73.911)       33
4952   (40.876, -73.91)       38
4953  (40.876, -73.909)       34
4954  (40.876, -73.908)       32
4955  (40.877, -73.913)       20
4956  (40.877, -73.912)       14
4957  (40.877, -73.911)       17
4958   (40.877, -73.91)       55
4959  (40.877, -73.909)      121
4960  (40.877, -73.907)        3

[4662 rows x 2 columns]

In [408]:
countsum = sum(countlocs.created)

In [409]:
countlocs['probs'] = countlocs.apply(lambda x: x['created']/countsum, axis=1)

In [410]:
countlocs.head()

latlong  created     probs
0  (40.678, -73.898)        1  0.000003
1   (40.68, -73.897)        6  0.000021
2  (40.687, -73.726)        3  0.000010
3  (40.689, -74.045)        2  0.000007
4   (40.69, -74.045)        1  0.000003

In [411]:
#percentage of all 311 calls included in prob threshold
# 0.0005 > 400 locs at 31%, 0.0025 > 1300 locs at 65%, 0.001 > 3000 locs at 91%, vs 4966 total locs
thres = 0.0001#25
sum(countlocs[countlocs.probs>thres].created)/countsum

0.91586111216562727

In [412]:
countlocs_thres = countlocs[countlocs.probs > thres]

In [413]:
countlocs_thres[countlocs_thres.latlong == (40.76, -73.961)]

latlong  created     probs
2075  (40.76, -73.961)       71  0.000245

In [414]:
mostlocs = set(countlocs[countlocs.probs>thres].latlong)

In [415]:
len(mostlocs)

2988

In [416]:
list(mostlocs)[0]

(40.719000000000001, -73.992000000000004)

In [247]:
for i,m in enumerate(mostlocs):
    if i<5:
        print(m)

(40.719000000000001, -73.992000000000004)
(40.759999999999998, -73.960999999999999)
(40.768999999999998, -73.957999999999998)
(40.779000000000003, -73.980000000000004)
(40.798999999999999, -73.968999999999994)


### load model and predict

In [ ]:
# And now to load...
scaler = joblib.load(scaler_filename) 

In [444]:
#use predictions to create 'map' of all locations, over time
# input has 5 features: lat, long, dayofweek, hourofday, month
import time
now = time.asctime( time.localtime(time.time()) )
print("Local current time :", now) #print (\"Current time %s\"  % now )
start = time.time()

preds = []# np.empty((1,6))
#for each moment in time
'''for m in range(1,13):#year:
    for d in range(7):#week:'''
d=2#6
m=2#7
for h in range(24):#day:
    #get predications for each location in manhattan based on lat/long
    for l,lo in mostlocs: # latlongs:#np.arange(minlat, maxlat+0.001, 0.001):
        #print(l,lo)
        #check if loc exists in time period:
        if len(df[df.latlong==(l,lo)][round(df.month)==m][df.day==d][round(df.hour)==h])>0:
            with tf.Session() as sess:
                saver.restore(sess, "./my_model_final4.ckpt") #final2 at 0.249 acc using minutes in hr and dates in mo
                #prepare input, scale...
                xes = scaler.transform(np.array([l,lo,d,h,m]))
                Z = logits.eval(feed_dict={X: xes.reshape(1, n_inputs)})
                pred = np.argmax(Z, axis=1)
            feat = features[pred[0]]
            preds.append([l,lo,d,h,m,feat])#np.vstack((preds, np.array([l,lo,h,d,m,feat])))
            #print(len(preds))
                    
print("took %d minutes and %d seconds to predict." % ((time.time() - start)/60, ((time.time()-start)%60)))
os.system('espeak "predictions done"')

Local current time : Tue Oct 24 01:17:58 2017


/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:19: UserWarning: Boolean Series key will be reindexed to match DataFrame index.


INFO:tensorflow:Restoring parameters from ./my_model_final4.ckpt


INFO:tensorflow:Restoring parameters from ./my_model_final4.ckpt
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)


INFO:tensorflow:Restoring parameters from ./my_model_final4.ckpt


...

INFO:tensorflow:Restoring parameters from ./my_model_final4.ckpt


INFO:tensorflow:Restoring parameters from ./my_model_final4.ckpt


took 52 minutes and 2 seconds to predict.

/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)


0

use following to get predictions over all times in chosen month

In [516]:
#use predictions to create 'map' of all locations, over time
# input has 5 features: lat, long, dayofweek, hourofday, month
import time
now = time.asctime( time.localtime(time.time()) )
print("Local current time :", now) #print (\"Current time %s\"  % now )
start = time.time()

preds = []# np.empty((1,6))
#for each moment in time
'''for m in range(1,13):#year:
    for d in range(7):#week:'''
#d=2#6
m=1 #5 #may
with tf.Session() as sess:
    saver.restore(sess, "./my_model_final4.ckpt") #final2 at 0.249 acc using minutes in hr and dates in mo
    for d in range(7):
        for h in range(24):#day:
            #get predications for each location in manhattan based on lat/long
            for l,lo in mostlocs: # latlongs:#np.arange(minlat, maxlat+0.001, 0.001):
                #print(l,lo)
                #check if loc exists in time period:
                if len(df[df.latlong==(l,lo)][round(df.month)==m][df.day==d][round(df.hour)==h])>0:
                    #prepare input, scale...
                    xes = scaler.transform(np.array([l,lo,d,h,m]))
                    Z = logits.eval(feed_dict={X: xes.reshape(1, n_inputs)})
                    pred = np.argmax(Z, axis=1)
                    feat = features[pred[0]]
                    preds.append([l,lo,d,h,m,feat])#np.vstack((preds, np.array([l,lo,h,d,m,feat])))
                    #print(len(preds))
                    
print("took %d minutes and %d seconds to predict." % ((time.time() - start)/60, ((time.time()-start)%60)))
os.system('espeak "predictions done"')

Local current time : Thu Oct 26 06:51:33 2017
INFO:tensorflow:Restoring parameters from ./my_model_final4.ckpt


INFO:tensorflow:Restoring parameters from ./my_model_final4.ckpt
/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:22: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing

/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.re

/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.re

/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.re

...

/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.re

/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.re

/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.reshape(1, -1) if it contains a single sample.
  warnings.warn(DEPRECATION_MSG_1D, DeprecationWarning)
/usr/local/lib/python3.5/dist-packages/sklearn/preprocessing/data.py:356: DeprecationWarning: Passing 1d arrays as data is deprecated in 0.17 and will raise ValueError in 0.19. Reshape your data either using X.reshape(-1, 1) if your data has a single feature or X.re

took 342 minutes and 20 seconds to predict.


0

In [517]:
preds = np.vstack(preds)

In [518]:
preds.shape

(12424, 6)

In [519]:
#get into pandas and add probs
predictions = pd.DataFrame(data=preds, columns=['lat','long','day','hour','month','complaint'])

In [520]:
predictions.head()

lat     long day hour month      complaint
0  40.819  -73.954   0    0     1  DOHMH: Rodent
1    40.8  -73.953   0    0     1  DOHMH: Rodent
2  40.836   -73.94   0    0     1  DOHMH: Rodent
3  40.825  -73.939   0    0     1  DOHMH: Rodent
4  40.734    -74.0   0    0     1  DOHMH: Rodent

In [425]:
#probability that location has complaint in general? or at that time
# look up each latlong in original DF for complaint at that time period.
#
len(df[df.latlong == (40.819,-73.954)][round(df.month)==7][df.day==6][round(df.hour)==0])


#predictions.groupby(['lat','long']).count()

/usr/local/lib/python3.5/dist-packages/ipykernel_launcher.py:4: UserWarning: Boolean Series key will be reindexed to match DataFrame index.
  after removing the cwd from sys.path.


2

In [280]:
predictions['prob'] = countlocs_thres.probs.values

In [521]:
predictions.tail()

lat     long day hour month                  complaint
12419   40.72  -73.979   6   23     1  NYPD: Noise - Residential
12420  40.733  -74.003   6   23     1   NYPD: Noise - Commercial
12421  40.793  -73.939   6   23     1  NYPD: Noise - Residential
12422  40.819  -73.942   6   23     1  NYPD: Noise - Residential
12423   40.71  -74.008   6   23     1  NYPD: Noise - Residential

In [522]:
predictions.groupby(['complaint']).count()

lat  long   day  hour  month
complaint                                                      
DEP: Noise                         643   643   643   643    643
DEP: Water System                  289   289   289   289    289
DHS: Homeless Person Assistance   1448  1448  1448  1448   1448
DOHMH: Food Poisoning               20    20    20    20     20
DOHMH: Non-Residential Heat          2     2     2     2      2
DOHMH: Rodent                      545   545   545   545    545
DOT: Curb Condition                 64    64    64    64     64
DOT: Street Condition              104   104   104   104    104
DOT: Street Light Condition         30    30    30    30     30
DPR: New Tree Request                2     2     2     2      2
DSNY: Snow                          60    60    60    60     60
FDNY: Fire Safety Director - F58     6     6     6     6      6
HPD: HEAT/HOT WATER               7121  7121  7121  7121   7121
HPD: PAINT/PLASTER                  18    18    18    18     18
HPD: PLUMBING                       16    16    16    16     16
NYPD: Illegal Parking              126   126   126   126    126
NYPD: Noise - Commercial           392   392   392   392    392
NYPD: Noise - Residential         1441  1441  1441  1441   1441
NYPD: Noise - Street/Sidewalk       96    96    96    96     96
NYPD: Vending                        1     1     1     1      1

In [452]:
predictions.groupby(['complaint','hour','lat','long']).count()

day  month
complaint                     hour lat    long               
DEP: Noise                    1    40.713 -73.998    1      1
                                   40.714 -73.998    1      1
                                   40.717 -74.004    1      1
                                   40.723 -73.995    1      1
                                   40.725 -74.002    1      1
                                   40.727 -73.985    1      1
                                          -73.991    1      1
                                   40.728 -73.994    1      1
                                          -73.995    1      1
                                   40.731 -74.004    1      1
                                   40.732 -73.984    1      1
                                   40.733 -73.987    1      1
                                   40.735 -74.004    1      1
                                   40.739 -73.984    1      1
                                   40.741 -73.983    1      1
                                   40.742 -73.978    1      1
                                   40.746 -74.005    1      1
                                   40.747 -73.985    1      1
                                   40.749 -73.984    1      1
                                   40.75  -73.996    1      1
                                   40.753 -73.975    1      1
                                          -73.979    1      1
                                   40.754 -73.999    1      1
                                   40.755 -73.976    1      1
                                   40.76  -73.974    1      1
                                          -73.989    1      1
                                   40.761 -73.966    1      1
                                   40.762 -73.965    1      1
                                   40.763 -73.967    1      1
                                          -73.976    1      1
...                                                ...    ...
NYPD: Noise - Residential     3    40.827 -73.944    1      1
                                   40.845 -73.935    1      1
                                   40.856 -73.927    1      1
                                          -73.929    1      1
                                   40.868 -73.923    1      1
                              4    40.72  -73.983    1      1
                                   40.721 -73.98     1      1
                                   40.794 -73.947    1      1
                                   40.877 -73.91     1      1
                              5    40.713 -73.983    1      1
                              8    40.713 -73.983    1      1
                                   40.715 -73.983    1      1
                              9    40.72  -73.978    1      1
NYPD: Noise - Street/Sidewalk 15   40.75  -73.986    1      1
                                   40.751 -73.984    1      1
                                   40.752 -73.983    1      1
                                          -73.984    1      1
                              16   40.753 -73.987    1      1
                                   40.755 -73.979    1      1
                              17   40.747 -73.987    1      1
                                   40.752 -73.982    1      1
                                          -73.986    1      1
                                   40.757 -73.986    1      1
                              18   40.75  -73.985    1      1
                                          -73.988    1      1
                                   40.752 -73.988    1      1
                                   40.755 -73.988    1      1
                                   40.76  -73.98     1      1
                              19   40.757 -73.986    1      1
                              20   40.753 -73.987    1      1

[4087 rows x 2 columns]

In [523]:
# save predictions into csv
predictions.to_csv('./preds_jan.csv', sep='\t')

In [524]:
#combine month predictions into one dataset:
import glob

combined = pd.DataFrame()
'''files =[]

for counter, file in enumerate(glob.glob('./preds_*')):
    #combined = combined.append(pd.read_csv(file, skiprows=0))#usecols=[]
    files.append = pd.read_csv(file, index_col=False)

combined = pd.concat(files)
    
combined.to_csv('./months_combined.csv')'''

combined = pd.concat(map(pd.read_csv, glob.iglob(os.path.join('', 'preds_*.csv'))), ignore_index=True) # for concat and index_col=None, header=0 for read_csv

combined.to_csv('./months_combined.csv')